In [7]:
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport
from sklearn.impute import KNNImputer


from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import confusion_matrix
from sklearn.naive_bayes import GaussianNB
from sklearn import svm

In [9]:
data

monthly_minutes  customerServiceCalls  streaming_minutes  TotalBilled  \
0               22604.0                   2.0            26525.0        285.0   
1               17059.0                   2.0            16887.0        201.0   
2               25848.0                   2.0            26783.0        264.0   
3               22080.0                   3.0            23649.0        274.0   
4               23871.0                   3.0             7705.0        236.0   
...                 ...                   ...                ...          ...   
100995          15244.0                   2.0            19118.0        270.0   
100996          16427.0                   1.0            22345.0        276.0   
100997          24106.0                   1.0            27419.0        268.0   
100998          14862.0                   2.0            28359.0        294.0   
100999           9588.0                   2.0            22497.0        240.0   

        PrevBalance  latePayments  ip_address_asn  phone_area_code  \
0              47.0           5.0         16767.0            253.0   
1              45.0           5.0         53966.0            241.0   
2              44.0           6.0         19278.0            232.0   
3              49.0           6.0         16680.0            236.0   
4              61.0           5.0         51308.0            243.0   
...             ...           ...             ...              ...   
100995         50.0           6.0         56225.0            259.0   
100996         58.0           4.0         54916.0            250.0   
100997         54.0           4.0         55589.0            262.0   
100998         56.0           4.0         14379.0            258.0   
100999         71.0           3.0         51185.0            248.0   

       customer_reg_date email_domain  ... maling_code paperlessBilling  \
0             2020-04-15    yahoo.com  ...           H               No   
1             2020-04-12    gmail.com  ...           V              Yes   
2             2020-02-22    gmail.com  ...           R              Yes   
3             2020-08-05    yahoo.com  ...           N               No   
4             2019-11-16    gmail.com  ...           V              Yes   
...                  ...          ...  ...         ...              ...   
100995        2020-09-06    gmail.com  ...           H               No   
100996        2020-07-05    gmail.com  ...           U               No   
100997        2020-05-12  hotmail.com  ...           U              Yes   
100998        2019-11-11    gmail.com  ...           P              Yes   
100999        2020-06-27    gmail.com  ...           C               No   

           paymentMethod      EVENT_TIMESTAMP     customerId  \
0           Mailed Check  2019-11-30 23:48:32  1-136-08562-9   
1           Mailed Check  2020-09-27 03:23:42  0-384-11264-1   
2            Credit Card  2020-01-12 15:18:38  0-08-151665-7   
3           Mailed Check  2020-10-09 18:07:46  0-02-200816-0   
4       Electronic Check  2020-10-17 22:27:42  0-87476-135-2   
...                  ...                  ...            ...   
100995  Electronic Check  2019-11-16 12:22:04  0-542-94214-3   
100996  Electronic Check  2019-11-29 07:47:44  1-4059-0436-4   
100997      Mailed Check  2020-01-03 06:18:32  0-03-923051-1   
100998      Mailed Check  2020-08-27 00:16:19  0-484-80062-0   
100999      Mailed Check  2019-11-25 05:35:59  1-266-52139-9   

                      billing_address  gender networkSpeed senior_citizen  \
0            5592 Gill Pine Suite 387  Female           5G            1.0   
1       5806 Kathleen Mount Suite 186    Male           5G            0.0   
2          5037 Allen Square Apt. 727    Male           5G            1.0   
3         841 Griffin Route Suite 824  Female           5G            0.0   
4          46185 Mejia Manor Apt. 558    Male        4Glte            1.0   
...                               ...     ...          ...    

In [10]:
for i in data.columns:
    if data[i].isnull().sum()/len(data) > 0.45:
         print(i)

In [11]:
for i in data.columns:
    if data[i].dtype not in [float,int]:
        print(i)

customer_reg_date
email_domain
phoneModel
billing_city
billing_state
partner
PhoneService
MultipleLines
streamingPlan
mobileHotspot
wifiCallingText
OnlineBackup
device_protection
contract_code
currency_code
maling_code
paperlessBilling
paymentMethod
EVENT_TIMESTAMP
customerId
billing_address
gender
networkSpeed
EVENT_LABEL


In [12]:
profile = ProfileReport(data, title="Pandas Profiling Report")
profile

Render HTML: 100%|██████████| 1/1 [00:05<00:00,  5.86s/it]


In [13]:
data1=data[['EVENT_LABEL','customerServiceCalls','streaming_minutes','TotalBilled','paymentMethod','currency_code']]

In [14]:
pd.crosstab(data1['EVENT_LABEL'], data1['paymentMethod'])

paymentMethod  Bank Transfer  Credit Card  Electronic Check  Mailed Check
EVENT_LABEL                                                              
fraud                    268          129              2811          2311
legit                    362         2727             32828         59537

In [15]:
pd.crosstab(data['EVENT_LABEL'], data['currency_code'])

currency_code    cad   eur   usd
EVENT_LABEL                     
fraud           3936  1382   199
legit          79498  8176  7778

In [16]:
pd.crosstab(data['EVENT_LABEL'], data['customerServiceCalls'])

customerServiceCalls   0.0    1.0    2.0   3.0  4.0
EVENT_LABEL                                        
fraud                  157   2065   2865   428    4
legit                 2011  37135  48455  7762   91

In [17]:
data1['EVENT_LABEL'] = data1['EVENT_LABEL'].map({'legit':0,'fraud':1})

In [18]:
print(data1.groupby('customerServiceCalls')['EVENT_LABEL'].mean())
print(data1.groupby('paymentMethod')['EVENT_LABEL'].mean())
print(data1.groupby('currency_code')['EVENT_LABEL'].mean())


customerServiceCalls
0.0    0.072417
1.0    0.052679
2.0    0.055826
3.0    0.052259
4.0    0.042105
Name: EVENT_LABEL, dtype: float64
paymentMethod
Bank Transfer       0.425397
Credit Card         0.045168
Electronic Check    0.078874
Mailed Check        0.037366
Name: EVENT_LABEL, dtype: float64
currency_code
cad    0.047175
eur    0.144591
usd    0.024947
Name: EVENT_LABEL, dtype: float64


In [19]:
data1.head()

EVENT_LABEL  customerServiceCalls  streaming_minutes  TotalBilled  \
0            0                   2.0            26525.0        285.0   
1            0                   2.0            16887.0        201.0   
2            0                   2.0            26783.0        264.0   
3            0                   3.0            23649.0        274.0   
4            0                   3.0             7705.0        236.0   

      paymentMethod currency_code  
0      Mailed Check           usd  
1      Mailed Check           eur  
2       Credit Card           cad  
3      Mailed Check           cad  
4  Electronic Check           cad

In [20]:
# target proportion encoding 

target_col='EVENT_LABEL'

for i in data1.columns:

    if data1[i].dtype in [object]:

        data1[i] = data1[i].map(dict(zip((data1.groupby(i)[target_col].mean().index), 
        (data1.groupby(i)[target_col].mean().values))))


In [21]:
data1.head()

EVENT_LABEL  customerServiceCalls  streaming_minutes  TotalBilled  \
0            0                   2.0            26525.0        285.0   
1            0                   2.0            16887.0        201.0   
2            0                   2.0            26783.0        264.0   
3            0                   3.0            23649.0        274.0   
4            0                   3.0             7705.0        236.0   

   paymentMethod  currency_code  
0       0.037366       0.024947  
1       0.037366       0.144591  
2       0.045168       0.047175  
3       0.037366       0.047175  
4       0.078874       0.047175

In [22]:
knn_imputer = KNNImputer(n_neighbors=5, weights='uniform', metric='nan_euclidean')

data1 = pd.DataFrame(knn_imputer.fit_transform(data1), columns=data1.columns)

In [23]:
data1.isnull().sum().sum()

0

In [24]:
data1

EVENT_LABEL  customerServiceCalls  streaming_minutes  TotalBilled  \
0               0.0                   2.0            26525.0        285.0   
1               0.0                   2.0            16887.0        201.0   
2               0.0                   2.0            26783.0        264.0   
3               0.0                   3.0            23649.0        274.0   
4               0.0                   3.0             7705.0        236.0   
...             ...                   ...                ...          ...   
100995          0.0                   2.0            19118.0        270.0   
100996          0.0                   1.0            22345.0        276.0   
100997          0.0                   1.0            27419.0        268.0   
100998          0.0                   2.0            28359.0        294.0   
100999          0.0                   2.0            22497.0        240.0   

        paymentMethod  currency_code  
0            0.037366       0.024947  
1            0.037366       0.144591  
2            0.045168       0.047175  
3            0.037366       0.047175  
4            0.078874       0.047175  
...               ...            ...  
100995       0.078874       0.047175  
100996       0.078874       0.047175  
100997       0.037366       0.047175  
100998       0.037366       0.047175  
100999       0.037366       0.047175  

[101000 rows x 6 columns]

In [25]:
# before rebalancing

In [26]:
y = data1['EVENT_LABEL']

x = data1.drop('EVENT_LABEL',axis=1)

In [27]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.30, random_state=0)

logisticRegr = LogisticRegression()
logisticRegr.fit(x_train, y_train)
y_pred=logisticRegr.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))


accuracy_score 0.9488778877887789
precision_score 0.7823529411764706
recall_score 0.08085106382978724
f1_score 0.1465564738292011


In [28]:
clf = RandomForestClassifier(n_estimators=100, max_depth=2, random_state=0)
clf.fit(x_train, y_train)
y_pred=clf.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.9457095709570957
precision_score 0.0
recall_score 0.0
f1_score 0.0


In [29]:
gnb = GaussianNB()
gnb.fit(x_train, y_train)
y_pred=gnb.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.948976897689769
precision_score 0.8413793103448276
recall_score 0.07416413373860183
f1_score 0.13631284916201117


In [30]:
clf2 = svm.SVC()
clf2.fit(x_train, y_train)
y_pred=clf2.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.9457095709570957
precision_score 0.0
recall_score 0.0
f1_score 0.0


In [31]:
(len(data1[data1.EVENT_LABEL ==1])) / (len(data))

0.05465346534653465

In [32]:
data1[data1.EVENT_LABEL ==1]

EVENT_LABEL  customerServiceCalls  streaming_minutes  TotalBilled  \
10              1.0                   2.0            29231.0        170.0   
23              1.0                   1.0            16493.0        151.0   
24              1.0                   2.0            28510.0        185.0   
53              1.0                   2.0            20336.0        239.0   
76              1.0                   1.0            21081.0        227.0   
...             ...                   ...                ...          ...   
100908          1.0                   1.0            19329.0        186.0   
100968          1.0                   2.0            32798.0        189.0   
100972          1.0                   2.0            15062.0        211.0   
100977          1.0                   2.0            17638.0        180.0   
100988          1.0                   2.0            20675.0        237.0   

        paymentMethod  currency_code  
10           0.037366       0.047175  
23           0.037366       0.047175  
24           0.078874       0.144591  
53           0.078874       0.047175  
76           0.037366       0.144591  
...               ...            ...  
100908       0.037366       0.047175  
100968       0.425397       0.144591  
100972       0.078874       0.047175  
100977       0.037366       0.047175  
100988       0.045168       0.047175  

[5520 rows x 6 columns]

In [33]:
data1[data1.EVENT_LABEL ==0].sample(frac=0.05)

EVENT_LABEL  customerServiceCalls  streaming_minutes  TotalBilled  \
69925          0.0                   2.0            17616.0        257.0   
15919          0.0                   3.0            26147.0        168.0   
42799          0.0                   2.0            24853.0        310.0   
80921          0.0                   2.0            20897.0        266.0   
56197          0.0                   2.0            20225.0        161.0   
...            ...                   ...                ...          ...   
37024          0.0                   2.0            16461.0        254.0   
64302          0.0                   2.0            23164.0        218.0   
43355          0.0                   2.0            28554.0        206.0   
37962          0.0                   2.0            20823.0        248.0   
71303          0.0                   2.0            19500.0        246.0   

       paymentMethod  currency_code  
69925       0.078874       0.047175  
15919       0.037366       0.144591  
42799       0.078874       0.047175  
80921       0.037366       0.047175  
56197       0.037366       0.047175  
...              ...            ...  
37024       0.078874       0.024947  
64302       0.037366       0.047175  
43355       0.037366       0.047175  
37962       0.037366       0.047175  
71303       0.078874       0.047175  

[4774 rows x 6 columns]

In [34]:
data3=pd.concat([data1[data1.EVENT_LABEL ==1], data1[data1.EVENT_LABEL ==0].sample(frac=0.05)])

data3

EVENT_LABEL  customerServiceCalls  streaming_minutes  TotalBilled  \
10             1.0                   2.0            29231.0        170.0   
23             1.0                   1.0            16493.0        151.0   
24             1.0                   2.0            28510.0        185.0   
53             1.0                   2.0            20336.0        239.0   
76             1.0                   1.0            21081.0        227.0   
...            ...                   ...                ...          ...   
23643          0.0                   1.0            26608.0        237.0   
34391          0.0                   2.0            23966.0        326.0   
91013          0.0                   2.0            23240.0        214.0   
93517          0.0                   2.0            14021.0        234.0   
33811          0.0                   2.0             8905.0        232.0   

       paymentMethod  currency_code  
10          0.037366       0.047175  
23          0.037366       0.047175  
24          0.078874       0.144591  
53          0.078874       0.047175  
76          0.037366       0.144591  
...              ...            ...  
23643       0.037366       0.047175  
34391       0.037366       0.047175  
91013       0.037366       0.047175  
93517       0.425397       0.047175  
33811       0.078874       0.024947  

[10294 rows x 6 columns]

In [35]:
data1=data3

In [36]:
# after rebalancing

y = data1['EVENT_LABEL']

x = data1.drop('EVENT_LABEL',axis=1)

In [37]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.30, random_state=0)

logisticRegr = LogisticRegression()
logisticRegr.fit(x_train, y_train)
y_pred=logisticRegr.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.6992554224668177
precision_score 0.7084601339013998
recall_score 0.7211895910780669
f1_score 0.7147681915873503


In [38]:
clf = RandomForestClassifier(n_estimators=100, max_depth=2, random_state=0)
clf.fit(x_train, y_train)
y_pred=clf.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.7559080608611201
precision_score 0.7289669861554846
recall_score 0.8482032218091697
f1_score 0.7840778923253151


In [39]:
gnb = GaussianNB()
gnb.fit(x_train, y_train)
y_pred=gnb.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.7523470378763354
precision_score 0.7540394973070018
recall_score 0.7806691449814126
f1_score 0.767123287671233


In [44]:
clf2 = svm.SVC()
clf2.fit(x_train, y_train)
y_pred=clf2.predict(x_test)

print('accuracy_score', accuracy_score(y_test, y_pred))
print('precision_score', precision_score(y_test, y_pred))
print('recall_score', recall_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

accuracy_score 0.6034315312398835
precision_score 0.6139425893380199
recall_score 0.6493184634448576
f1_score 0.6311352002408913


In [41]:
# best method is RandomForestClassifier f1 score = 0,78